In [1]:
import pandas as pd
import numpy as np
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [2]:
train_data = pd.read_parquet('../../data/non-null/df_13_months_unprocessed_non_null.parquet')
# test_data = pd.read_parquet('../../data/non-null/test_data_10_months_unprocessed_non_null.parquet')


In [4]:
train_data[train_data['customer_ID'] == '0009bd8871169b8d76a445e1f52079a6edc0b6f0bf021d5ec50ef6aa6487cc14']

customer_ID        S_2      D_39  \
762  0009bd8871169b8d76a445e1f52079a6edc0b6f0bf021d... 2018-03-24  0.007035   

          B_1       R_1       B_4       B_5       R_2      D_47       B_7  \
762  0.003712  0.507655  0.137897  0.007317  1.000958  0.555546  0.228845   

         D_51       B_9     R_3      B_10       S_5      B_11       S_6  \
762  0.008856  0.009752  0.5003  0.028748  0.004802  0.003663  1.005175   

          R_4      B_12       S_8       R_5      D_58      B_14      D_60  \
762  1.005408  0.010627  0.002524  0.502572  0.474101  0.001786  0.001743   

        S_11 D_63      D_65      B_18      S_12       R_6      S_13      B_21  \
762  0.28719   CO  0.005823  0.585338  0.185295  0.126165  0.004588  0.009585   

         D_71      S_15      B_23       P_4      D_75     B_24       R_7  \
762  0.026944  0.507485  0.211864  0.960185  0.276619  0.00842  0.143661   

          R_8      S_16      R_10      R_11      S_17      R_12      B_28  \
762  1.007309  0.004571  0.005379  0.007175  0.007402  1.004646  0.140864   

        R_13      R_14     R_15     R_16      S_18      D_86     R_17  \
762  0.00256  0.001873  0.00093  0.00407  0.003437  0.009765  0.00251   

         R_18  B_31      S_19      R_19      B_32      S_20      R_20  \
762  0.001234     1  0.000541  0.004018  0.008412  0.009376  0.008711   

         R_21      R_22      R_23      D_92      D_93     D_94      R_24  \
762  0.002895  0.009052  0.002215  0.005987  0.006823  0.00123  0.001069   

        R_25      D_96      S_26    D_102      B_36      B_37      B_40  \
762  0.00579  0.003505  0.006911  0.81086  0.009654  0.005641  0.094856   

     D_126     D_127      B_41     D_133      R_28     D_140     D_144  \
762    0.0  0.009784  0.008053  0.004038  0.006742  0.005503  0.007178   

     target end_of_month  
762       0   2018-03-31

In [5]:
# train and val ids
train_ids = pd.read_csv('../../data/initial_modelling/ids/train_target.csv')['customer_ID'].values
val_ids = pd.read_csv('../../data/initial_modelling/ids/val_target.csv')['customer_ID'].values
test_ids = pd.read_csv('../../data/initial_modelling/ids/test_target.csv')['customer_ID'].values

In [6]:
train_data_filtered = train_data[train_data['customer_ID'].isin(train_ids)]
val_data_filtered = train_data[train_data['customer_ID'].isin(val_ids)]
test_data_filtered = train_data[train_data['customer_ID'].isin(test_ids)]

In [7]:
train_data_filtered.info(verbose=True, show_counts=True, memory_usage=True)

<class 'pandas.core.frame.DataFrame'>
Index: 3486098 entries, 0 to 5531450
Data columns (total 83 columns):
 #   Column        Non-Null Count    Dtype         
---  ------        --------------    -----         
 0   customer_ID   3486098 non-null  object        
 1   S_2           3486098 non-null  datetime64[ns]
 2   D_39          3486098 non-null  float32       
 3   B_1           3486098 non-null  float32       
 4   R_1           3486098 non-null  float32       
 5   B_4           3486098 non-null  float32       
 6   B_5           3486098 non-null  float32       
 7   R_2           3486098 non-null  float32       
 8   D_47          3486098 non-null  float32       
 9   B_7           3486098 non-null  float32       
 10  D_51          3486098 non-null  float32       
 11  B_9           3486098 non-null  float32       
 12  R_3           3486098 non-null  float32       
 13  B_10          3486098 non-null  float32       
 14  S_5           3486098 non-null  float32       
 15  B_1

In [8]:
#Fill null values with 0
train_data_filtered = train_data_filtered.fillna(0)
val_data_filtered = val_data_filtered.fillna(0)
test_data_filtered = test_data_filtered.fillna(0)

In [9]:
train_data_filtered.isna().sum().sum(), val_data_filtered.isna().sum().sum(), test_data_filtered.isna().sum().sum()

(0, 0, 0)

In [10]:
from sklearn.preprocessing import OneHotEncoder
import pandas as pd
import numpy as np

def one_hot_encode_categories(df, categorical_columns=None, drop_original=True, handle_unknown='error'):
    """
    One-hot encode categorical columns in a DataFrame.
    
    Parameters:
    -----------
    df : pandas.DataFrame
        Input DataFrame containing categorical columns
    categorical_columns : list or None
        List of categorical column names to encode. If None, automatically detects categorical columns.
    drop_original : bool
        Whether to drop the original categorical columns
    handle_unknown : str
        Strategy for handling unknown categories in new data: 'error', 'ignore' or 'infrequent_if_exist'
    
    Returns:
    --------
    pandas.DataFrame
        DataFrame with one-hot encoded columns
    OneHotEncoder
        Fitted encoder for future transformations
    """
    # Make a copy to avoid modifying the original
    result_df = df.copy()
    
    # Automatically detect categorical columns if not specified
    if categorical_columns is None:
        categorical_columns = result_df.select_dtypes(include=['object', 'category']).columns.tolist()
    
    if not categorical_columns:
        print("No categorical columns found to encode.")
        return result_df, None
        
    # Initialize the encoder
    encoder = OneHotEncoder(sparse_output=False, handle_unknown=handle_unknown, drop='if_binary')
    
    # Fit and transform the categorical columns
    encoded_array = encoder.fit_transform(result_df[categorical_columns])
    
    # Get feature names
    feature_names = encoder.get_feature_names_out(categorical_columns)
    
    # Create a DataFrame with the encoded features
    encoded_df = pd.DataFrame(encoded_array, columns=feature_names, index=result_df.index)
    
    # Combine with the original DataFrame
    if drop_original:
        # Drop the original categorical columns
        result_df = result_df.drop(columns=categorical_columns)
    
    # Concatenate the encoded columns with the original DataFrame
    result_df = pd.concat([result_df, encoded_df], axis=1)
    
    print(f"One-hot encoded {len(categorical_columns)} categorical columns into {len(feature_names)} binary features.")
    
    return result_df, encoder

In [11]:
cat_cols = ['D_126', 'D_63']
train_data_filtered[cat_cols] = train_data_filtered[cat_cols].astype('category')
val_data_filtered[cat_cols] = val_data_filtered[cat_cols].astype('category')
test_data_filtered[cat_cols] = test_data_filtered[cat_cols].astype('category')

In [12]:
ohe = OneHotEncoder(handle_unknown='ignore', sparse_output=False, drop='if_binary')
ohe.fit_transform(train_data_filtered[cat_cols])

array([[0., 0., 1., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.],
       ...,
       [0., 0., 1., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.]])

In [13]:
ohe.get_feature_names_out(cat_cols)

array(['D_126_-1.0', 'D_126_0.0', 'D_126_1.0', 'D_63_CL', 'D_63_CO',
       'D_63_CR', 'D_63_XL', 'D_63_XM', 'D_63_XZ'], dtype=object)

In [14]:
# Apply to your training data
train_data_filtered_oh, cat_encoder = one_hot_encode_categories(train_data_filtered, handle_unknown='ignore', categorical_columns=cat_cols)

One-hot encoded 2 categorical columns into 9 binary features.


In [15]:
val_data_filtered_oh = pd.concat([val_data_filtered.drop(columns=cat_encoder.feature_names_in_),pd.DataFrame(cat_encoder.transform(val_data_filtered[cat_encoder.feature_names_in_]), columns=cat_encoder.get_feature_names_out(),index=val_data_filtered.index)], axis=1)
test_data_filtered_oh = pd.concat([test_data_filtered.drop(columns=cat_encoder.feature_names_in_),pd.DataFrame(cat_encoder.transform(test_data_filtered[cat_encoder.feature_names_in_]), columns=cat_encoder.get_feature_names_out(),index=test_data_filtered.index)], axis=1)

In [16]:
test_data_filtered_oh.head()

customer_ID        S_2      D_39  \
13  00000fd6641609c6ece5454664794f0340ad84dddce9a2... 2017-03-01  0.382790   
14  00000fd6641609c6ece5454664794f0340ad84dddce9a2... 2017-04-16  0.002224   
15  00000fd6641609c6ece5454664794f0340ad84dddce9a2... 2017-05-07  0.567403   
16  00000fd6641609c6ece5454664794f0340ad84dddce9a2... 2017-06-25  0.213193   
17  00000fd6641609c6ece5454664794f0340ad84dddce9a2... 2017-07-30  0.325467   

         B_1       R_1       B_4       B_5       R_2      D_47       B_7  \
13  0.025782  0.005515  0.021776  0.070967  0.008058  0.382562  0.032390   
14  0.006806  0.003287  0.012991  0.026492  0.006785  0.386114  0.024356   
15  0.033713  0.005594  0.015447  0.031776  0.008117  0.384930  0.034360   
16  0.031170  0.008996  0.015686  0.057811  0.007326  0.389402  0.028317   
17  0.109644  0.008041  0.046556  0.029022  0.009446  0.388776  0.068204   

        D_51       B_9       R_3      B_10       S_5      B_11       S_6  \
13  0.334386  0.007561  0.005552  0.302757  0.025802  0.011677  0.003243   
14  0.672143  0.004459  0.001319  0.295964  0.004938  0.000887  0.006905   
15  0.666925  0.010246  0.002729  0.296058  0.011832  0.017219  0.007552   
16  0.340447  0.010398  0.008935  0.294000  0.036272  0.012104  0.000044   
17  0.341473  0.045093  0.002589  0.301472  0.052949  0.081246  0.004738   

         R_4      B_12       S_8       R_5      D_58      B_14      D_60  \
13  0.001485  0.026337  0.596242  0.004105  0.007069  0.015918  0.375191   
14  0.000638  0.019455  0.472848  0.000791  0.004691  0.005317  0.295413   
15  0.004912  0.022642  0.666716  0.005254  0.006135  0.016580  0.446750   
16  0.003507  0.025763  0.762724  0.004414  0.005296  0.018577  0.333445   
17  0.000154  0.022630  0.763803  0.007880  0.007024  0.057174  0.857541   

        S_11      D_65      B_18      S_12       R_6      S_13      B_21  \
13  0.281806  0.007912  1.008107  0.175123  0.000396  0.282619  0.006760   
14  0.368255  0.006940  1.007984  0.133366  0.004131  0.006044  0.003196   
15  0.408506  0.004088  1.009827  0.181359  0.004799  0.428290  0.004767   
16  0.282240  0.000637  1.003075  0.344811  0.001317  0.282940  0.009902   
17  0.209741  0.001527  1.003711  0.175933  0.008271  0.286403  0.001140   

        D_71      S_15      B_23       P_4      D_75      B_24       R_7  \
13  0.015735  0.200131  0.014834  0.004637  0.000939  0.000798  0.000963   
14  0.009996  0.205070  0.009042  0.009077  0.001021  0.005710  0.001982   
15  0.014169  0.208094  0.020937  0.003788  0.007836  0.001452  0.003067   
16  0.008914  0.101021  0.013094  0.003013  0.006118  0.007651  0.009390   
17  0.005655  0.100353  0.043991  0.008953  0.007770  0.001539  0.005445   

         R_8      S_16      R_10      R_11      S_17      R_12      B_28  \
13  0.009420  0.001228  0.000954  0.008326  0.000797  1.002751  0.020552   
14  0.003919  0.003258  0.004326  0.001358  0.003771  1.006914  0.012105   
15  0.005586  0.003000  0.007756  0.004264  0.002065  1.005440  0.018039   
16  0.004440  0.007752  0.008919  0.004406  0.007113  1.008088  0.018089   
17  0.007108  0.001394  0.004627  0.009922  0.009012  1.002697  0.028811   

        R_13      R_14      R_15      R_16      S_18      D_86      R_17  \
13  0.007203  0.001399  0.003912  0.004460  0.003757  0.002582  0.007083   
14  0.001203  0.009384  0.009396  0.002898  0.001069  0.009929  0.007837   
15  0.002608  0.005944  0.000371  0.002720  0.006893  0.006179  0.008268   
16  0.006692  0.007051  0.006375  0.005186  0.009890  0.006215  0.003785   
17  0.008732  0.000852  0.009575  0.004130  0.002780  0.000137  0.002932   

        R_18  B_31      S_19      R_19      B_32      S_20      R_20  \
13  0.004040     1  0.002157  0.009864  0.005578  0.008184  0.000000   
14  0.003902     1  0.008078  0.004189  0.000256  0.005347  0.000296   
15  0.001903     1  0.000952  0.001200  0.002534  0.002703  0.003717   
16  0.009991     1  0.005835  0.001468  0.003205  0.008242  0.003763   
17  0.001728  

In [17]:
val_data_filtered_oh.head()

customer_ID        S_2      D_39  \
557  0006a80d96aec1d178bf74adab6cbf9e4bf427a6ba264f... 2017-03-23  0.008159   
558  0006a80d96aec1d178bf74adab6cbf9e4bf427a6ba264f... 2017-04-11  0.006427   
559  0006a80d96aec1d178bf74adab6cbf9e4bf427a6ba264f... 2017-05-23  0.036537   
560  0006a80d96aec1d178bf74adab6cbf9e4bf427a6ba264f... 2017-06-22  1.799837   
561  0006a80d96aec1d178bf74adab6cbf9e4bf427a6ba264f... 2017-07-22  0.006533   

          B_1       R_1       B_4       B_5       R_2      D_47       B_7  \
557  0.007563  0.507226  0.090289  0.190986  1.007860  0.173779  0.083620   
558  0.019910  0.509301  0.108799  0.187175  1.005072  0.172403  0.079490   
559  0.012582  0.502016  0.148967  0.001256  1.000259  0.173992  0.102289   
560  0.016483  0.507214  0.154814  0.007901  1.002629  0.174783  0.118236   
561  0.003690  0.502014  0.142666  0.001955  1.008437  0.175221  0.101416   

         D_51       B_9       R_3      B_10       S_5      B_11       S_6  \
557  0.005359  0.008166  0.008891  0.131589  0.005975  0.000981  0.000016   
558  0.008728  0.004247  0.008343  0.132400  0.001271  0.003537  0.004330   
559  0.000353  0.007659  0.004119  0.054929  0.009244  0.011092  0.007543   
560  0.000283  0.008381  0.009471  0.050791  0.007893  0.004834  0.000811   
561  0.006476  0.005372  0.000266  0.070988  0.000345  0.008381  0.005062   

          R_4      B_12       S_8       R_5      D_58      B_14      D_60  \
557  1.003291  0.046776  0.005546  0.505330  0.441886  0.000806  0.002399   
558  1.003840  0.055230  0.169339  0.508124  0.438819  0.013499  0.109257   
559  1.005890  0.049022  0.000524  0.505892  0.480702  0.022442  0.083639   
560  0.000447  0.047296  0.000436  0.001040  0.488948  0.017242  0.085385   
561  0.009213  0.046732  0.000631  0.002027  0.490288  0.007119  0.007480   

         S_11      D_65      B_18      S_12       R_6      S_13      B_21  \
557  0.283934  0.004346  0.654608  0.191767  0.026972  0.000548  0.004991   
558  0.081321  0.008174  0.646282  0.187604  0.022829  0.288559  0.004385   
559  0.285684  0.925472  0.321261  0.185135  0.032375  0.001317  0.009426   
560  0.286268  0.056950  0.235430  0.192209  0.062300  0.001918  0.009316   
561  0.287857  0.002004  0.653230  0.187660  0.055180  0.009487  0.007626   

         D_71      S_15      B_23       P_4      D_75      B_24       R_7  \
557  0.206801  0.507059  0.061024  0.003893  0.267714  0.001054  0.146232   
558  0.205893  0.905581  0.057464  0.005005  0.267826  0.004331  0.141768   
559  0.207621  0.506808  0.081206  0.005600  0.267144  0.009994  0.151137   
560  0.209325  0.508015  0.088857  0.002684  0.271750  0.003907  0.002679   
561  0.205901  0.506406  0.086959  0.001764  0.275320  1.906572  0.002207   

          R_8      S_16      R_10      R_11      S_17      R_12      B_28  \
557  1.000346  0.005446  0.007267  0.009887  0.004778  1.000392  0.055943   
558  0.009653  0.007440  0.001005  0.002605  0.003298  1.002665  0.059104   
559  0.003653  0.000624  0.009698  0.004655  0.007786  1.006245  0.075532   
560  0.008262  0.001076  0.001792  0.001913  0.007447  1.009832  0.085246   
561  0.005457  0.002737  0.005426  0.004660  0.000478 -0.073181  0.073047   

         R_13      R_14      R_15      R_16      S_18      D_86      R_17  \
557  0.009934  0.008194  0.000002  0.008703  1.009084  0.007760  0.004592   
558  0.037049  0.004004  0.007072  0.005467  1.008521  0.005276  0.004043   
559  0.008723  0.008765  0.008385  0.003891  1.009063  0.008859  0.034713   
560  0.003205  1.060993  0.002149  0.002440  1.008492  0.001500  0.007316   
561  0.002097  1.100851  0.009048  0.006141  1.005714  0.007667  0.009561   

         R_18  B_31      S_19      R_19      B_32      S_20      R_20  \
557  0.005844     1  0.008329  0.001857  0.003834  0.006580  0.002673   
558  0.004089     1  0.001243  0.003822  0.000133  0.000100  0.007396   
559  0.002099     1  0.004691  0.000010  0.000813  0.007615  0.006221   
560  0.008728     1  0.000524  0.00

In [18]:
train_data_filtered_oh.info(verbose=True, show_counts=True, memory_usage=True)

<class 'pandas.core.frame.DataFrame'>
Index: 3486098 entries, 0 to 5531450
Data columns (total 90 columns):
 #   Column        Non-Null Count    Dtype         
---  ------        --------------    -----         
 0   customer_ID   3486098 non-null  object        
 1   S_2           3486098 non-null  datetime64[ns]
 2   D_39          3486098 non-null  float32       
 3   B_1           3486098 non-null  float32       
 4   R_1           3486098 non-null  float32       
 5   B_4           3486098 non-null  float32       
 6   B_5           3486098 non-null  float32       
 7   R_2           3486098 non-null  float32       
 8   D_47          3486098 non-null  float32       
 9   B_7           3486098 non-null  float32       
 10  D_51          3486098 non-null  float32       
 11  B_9           3486098 non-null  float32       
 12  R_3           3486098 non-null  float32       
 13  B_10          3486098 non-null  float32       
 14  S_5           3486098 non-null  float32       
 15  B_1

In [19]:
cols_drop = ['S_2', 'target']

In [20]:
train_targets = train_data_filtered_oh[['customer_ID', 'end_of_month','target']]
val_targets = val_data_filtered_oh[['customer_ID', 'end_of_month','target']]
test_targets = test_data_filtered_oh[['customer_ID', 'end_of_month','target']]

In [21]:
train_data_filtered_oh.drop(columns=cols_drop, inplace=True)
val_data_filtered_oh.drop(columns=cols_drop, inplace=True)
test_data_filtered_oh.drop(columns=cols_drop, inplace=True)

In [22]:
train_data_filtered_oh.info(verbose=True, show_counts=True, memory_usage=True)

<class 'pandas.core.frame.DataFrame'>
Index: 3486098 entries, 0 to 5531450
Data columns (total 88 columns):
 #   Column        Non-Null Count    Dtype         
---  ------        --------------    -----         
 0   customer_ID   3486098 non-null  object        
 1   D_39          3486098 non-null  float32       
 2   B_1           3486098 non-null  float32       
 3   R_1           3486098 non-null  float32       
 4   B_4           3486098 non-null  float32       
 5   B_5           3486098 non-null  float32       
 6   R_2           3486098 non-null  float32       
 7   D_47          3486098 non-null  float32       
 8   B_7           3486098 non-null  float32       
 9   D_51          3486098 non-null  float32       
 10  B_9           3486098 non-null  float32       
 11  R_3           3486098 non-null  float32       
 12  B_10          3486098 non-null  float32       
 13  S_5           3486098 non-null  float32       
 14  B_11          3486098 non-null  float32       
 15  S_6

In [23]:
num_scale_drop_cols = ['customer_ID', 'end_of_month']+cat_encoder.get_feature_names_out().tolist()
print(num_scale_drop_cols)

['customer_ID', 'end_of_month', 'D_126_-1.0', 'D_126_0.0', 'D_126_1.0', 'D_63_CL', 'D_63_CO', 'D_63_CR', 'D_63_XL', 'D_63_XM', 'D_63_XZ']


In [24]:
len(num_scale_drop_cols)

11

In [25]:
from sklearn.preprocessing import RobustScaler
rb_scaler = RobustScaler()
rb_scaler.fit(train_data_filtered_oh.drop(columns=num_scale_drop_cols))

RobustScaler()

In [26]:
#Train data - numerically scaled
train_data_filtered_num_scaled = pd.DataFrame(rb_scaler.transform(train_data_filtered_oh.drop(columns=num_scale_drop_cols)), columns=train_data_filtered_oh.drop(columns=num_scale_drop_cols).columns, index=train_data_filtered_oh.index)
train_data_filtered_scaled = pd.concat([train_data_filtered_oh[num_scale_drop_cols], train_data_filtered_num_scaled], axis=1)

In [27]:
val_data_filtered_num_scaled = pd.DataFrame(rb_scaler.transform(val_data_filtered_oh.drop(columns=num_scale_drop_cols)), columns=val_data_filtered_oh.drop(columns=num_scale_drop_cols).columns, index=val_data_filtered_oh.index)
val_data_filtered_scaled = pd.concat([val_data_filtered_oh[num_scale_drop_cols], val_data_filtered_num_scaled], axis=1)

In [28]:
test_data_filtered_num_scaled = pd.DataFrame(rb_scaler.transform(test_data_filtered_oh.drop(columns=num_scale_drop_cols)), columns=test_data_filtered_oh.drop(columns=num_scale_drop_cols).columns, index=test_data_filtered_oh.index)
test_data_filtered_scaled = pd.concat([test_data_filtered_oh[num_scale_drop_cols], test_data_filtered_num_scaled], axis=1)

In [29]:
train_data_filtered_scaled.head()

customer_ID end_of_month  D_126_-1.0  \
0  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-03-31         0.0   
1  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-04-30         0.0   
2  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-05-31         0.0   
3  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-06-30         0.0   
4  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-07-31         0.0   

   D_126_0.0  D_126_1.0  D_63_CL  D_63_CO  D_63_CR  D_63_XL  D_63_XM  D_63_XZ  \
0        0.0        1.0      0.0      0.0      1.0      0.0      0.0      0.0   
1        0.0        1.0      0.0      0.0      1.0      0.0      0.0      0.0   
2        0.0        1.0      0.0      0.0      1.0      0.0      0.0      0.0   
3        0.0        1.0      0.0      0.0      1.0      0.0      0.0      0.0   
4        0.0        1.0      0.0      0.0      1.0      0.0      0.0      0.0   

       D_39       B_1       R_1       B_4       B_5       R_2      D_47  \
0 -0.031530 -0.193358  0.596697 -0.005885  3.340046  0.187636  0.430097   
1 -0.014119 -0.225782  0.063588 -0.060652  2.105628  0.187949  0.417851   
2  0.355170 -0.083059  0.178637 -0.063400  0.970532 -0.376162  0.427723   
3 -0.028421 -0.151057 -0.764522 -0.125940  3.257882  0.898597  0.447008   
4 -0.028301 -0.138175  0.315446 -0.205331  2.759657  0.276334  0.442083   

        B_7      D_51       B_9       R_3      B_10       S_5      B_11  \
0 -0.068261  3.996979 -0.054152 -0.040833 -0.052995  0.149665 -0.175099   
1 -0.075150  4.008827 -0.053645 -0.037962 -0.039543  0.259303 -0.175295   
2 -0.079670  4.000960 -0.050662 -0.010162  0.089044  0.529219 -0.098636   
3 -0.110135  4.009173 -0.058483 -0.030140  0.090408  0.251175 -0.102930   
4 -0.111515  4.014668 -0.077525 -0.041144  0.041932  0.618148 -0.104838   

        S_6       R_4      B_12       S_8       R_5      D_58      B_14  \
0  0.265639  0.617140  2.203041  1.234022 -0.634758  0.140691 -0.109645   
1 -0.622564  0.001057  2.122048  1.226667 -0.687565  0.113046 -0.167541   
2 -0.919454  0.356623  2.010618  1.396104  0.229017  0.088659  0.304506   
3 -0.880932  0.696510  1.873858  0.784626 -0.032887  0.084837 -0.173346   
4  0.018621 -0.250316  1.882784  1.221985 -0.679123  0.053094 -0.006697   

       D_60      S_11      D_65      B_18       S_12       R_6      S_13  \
0 -0.053285  0.673062  0.364595  0.008002   3.698888  0.611781  1.195362   
1 -0.125443  0.701377 -0.537467  0.000607  -0.084663 -0.223100  1.180760   
2  0.105704  0.704036 -0.639904 -0.000992  13.873399  0.318061  1.583316   
3  0.057333  0.694454  0.129630  0.009726  14.482219  0.577208  1.195503   
4 -0.003186  1.189373  0.814958  0.004396   1.170038  0.658594  1.177601   

       B_21      D_71      S_15      B_23       P_4      D_75      B_24  \
0 -0.482098  4.742827 -0.987669 -0.038312  0.290977 -0.020342 -0.163980   
1 -0.178518  5.686295 -1.012066 -0.083648 -0.174785 -0.000893 -0.187970   
2 -0.738326  2.806057 -1.004595 -0.053236  0.120958  0.008045 -0.656173   
3  0.707808  6.113277 -0.657595 -0.121804  0.633966 -0.010881  0.081326   
4  0.336550  3.721289 -0.995243 -0.117328  0.393854  0.000122 -0.046685   

        R_7       R_8      S_16      R_10      R_11      S_17      R_12  \
0  0.472729 -0.719102 -0.555217  0.356954 -0.546879  0.495977  0.966244   
1  0.032697 -0.900170  0.922050  0.136778 -0.927380 -0.859088  0.895532   
2 -0.723368  0.624448  0.834278  0.037921  0.355930 -0.245017 -0.109985   
3  0.239121  0.009118 -0.044802 -0.640310 -0.084314  0.297774 -0.024969   
4 -0.059365  0.436937  0.458947  0.164512 -0.585591 -0.670997 -0.768646   

       B_28      R_13      R_14      R_15      R_16      S_18      D_86  \
0  0.044994 -0.242766 -0.912997  0.270655 -0.066058  0.114598  0.371542   
1  0.027997 -0.931162 -0.149846 -0.540732 -0.306811  0.478112  0.292729   
2  0.028658 -0.462864  0.407523  0.646182  0.364257  0.149794 -0.770361   
3 -0.098960  0.978551  0.713006  0.450310  0.627054 -0.

In [30]:
# Group by customer_ID and count the number of unique months for each ID
customer_month_counts = train_data_filtered_scaled.groupby('customer_ID')['end_of_month'].nunique()

# Filter IDs that do not have complete 13 months
incomplete_ids = customer_month_counts[customer_month_counts < 13]

# Count how many IDs have incomplete data
num_incomplete_ids = len(incomplete_ids)

print(f"Number of customer_IDs with incomplete 13 months: {num_incomplete_ids}")

Number of customer_IDs with incomplete 13 months: 45876


In [31]:
incomplete_ids

customer_ID
000391f219520dbca6c3c1c46e0fab569da163f79ee266b2cc95fb31029ce617     4
00057c2d8d887fa3f777d97dc939700731575772e6c99025aaa0ab56870353ce     4
0005a6ae24fd274640a237ea56c43b1ef9e32077ad168a90d464dcf2bd5976fb    12
00062483fb33d6129dd4ee7e5a12f751d2e7010ac0df0178997c628883695603     8
000772ede38fe3811dea0dff9dc50e2f8b7b577ab6f143c034b2dbccee197f57    10
0009bd8871169b8d76a445e1f52079a6edc0b6f0bf021d5ec50ef6aa6487cc14     1
000b30e00a2a37b5ae325fa3830c9b2b6365b0c17719c9d283d66c0fd2284f59     7
000c36f7b5130de63c1b7ee4bc902ba51aa8ae1f9cd1cee254892b0b06011cb4    10
000de143ca96be8fa6362e55dffe94a0bdaf347d993160fb1e11208d7ecc0597    12
000eee12732c9c7b790870c556bc33339d6d17725cbeb4a7da6b2a5d2c8386aa     1
000f8fcfe7ca030fc553a55027ecdd0219fc8e2794c9af713f1ace182fd3064d     7
001089806583b378098bd81a88eb877a821202b1dfe257f963835d803c4debf0     8
00144998273d201cca895e6b7cf7f637abfbcff9fb59c757c54f7a245e00c3cc    12
00147acd28d88cc2e85209eef8b2001aed34d811e76ff1218dc7eb482f00e1fe 

In [32]:
train_data_filtered_oh.describe()

D_39           B_1           R_1           B_4           B_5  \
count  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06   
mean   1.531488e-01  1.241483e-01  7.898561e-02  1.723615e-01  8.303261e-02   
min    5.026190e-09 -7.588799e+00  1.534223e-09  3.099332e-09  9.308199e-10   
25%    4.525242e-03  8.863508e-03  2.893426e-03  2.755177e-02  7.291238e-03   
50%    9.053070e-03  3.139161e-02  5.784361e-03  8.222928e-02  1.539307e-02   
75%    2.366743e-01  1.260926e-01  8.664126e-03  2.387584e-01  5.375981e-02   
max    5.389619e+00  1.324060e+00  3.256284e+00  6.091593e+00  1.442070e+02   
std    2.702614e-01  2.122017e-01  2.266668e-01  2.216656e-01  3.967983e-01   

                R_2          D_47           B_7          D_51           B_9  \
count  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06   
mean   4.766352e-02  4.074914e-01  1.862180e-01  1.450415e-01  1.898576e-01   
min    8.265748e-10 -2.662164e-02 -2.652749e+00  3.351734e-09  1.525222e-08   
25%    2.615333e-03  2.324826e-01  2.827083e-02  3.642427e-03  5.748935e-03   
50%    5.223970e-03  3.834774e-01  7.598256e-02  7.281982e-03  2.601768e-02   
75%    7.838545e-03  5.623466e-01  2.709704e-01  3.360369e-01  3.346583e-01   
max    1.010000e+00  1.643096e+00  1.252750e+00  2.676606e+00  2.742486e+01   
std    2.021118e-01  2.349985e-01  2.305214e-01  2.420773e-01  2.863219e-01   

                R_3          B_10           S_5          B_11           S_6  \
count  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06   
mean   1.211345e-01  2.354816e-01  8.812562e-02  1.111240e-01  2.444899e-01   
min    2.238322e-09 -2.958413e-03  8.168135e-09  2.366277e-08  7.310181e-09   
25%    4.709538e-03  2.902998e-02  5.639581e-03  6.604757e-03  3.287534e-03   
50%    9.415087e-03  1.103424e-01  1.352873e-02  1.950601e-02  6.575177e-03   
75%    2.004473e-01  2.955373e-01  7.146916e-02  1.021959e-01  9.862134e-03   
max    1.160260e+01  4.097441e+03  1.292760e+02  1.767753e+00  1.010000e+00   
std    2.100950e-01  5.480628e+00  3.895789e-01  2.084680e-01  4.267806e-01   

                R_4          B_12           S_8           R_5          D_58  \
count  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06   
mean   3.127874e-02  9.411107e-02  3.274974e-01  3.477855e-02  2.157162e-01   
min    4.268393e-10  3.343624e-08  1.773123e-08  1.770989e-08  4.968945e-09   
25%    2.565390e-03  1.087140e-02  7.633024e-03  2.574548e-03  5.870325e-03   
50%    5.130752e-03  1.944105e-02  3.216822e-01  5.149283e-03  1.069447e-01   
75%    7.698233e-03  6.934739e-02  4.949142e-01  7.722161e-03  3.731091e-01   
max    1.010000e+00  4.207490e+02  1.231405e+00  3.500452e+01  1.261935e+00   
std    1.599943e-01  9.632324e-01  3.031561e-01  2.587034e-01  2.602299e-01   

               B_14          D_60          S_11          D_65          B_18  \
count  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06   
mean   1.011732e-01  3.755035e-01  3.751401e-01  3.968943e-02  5.958821e-01   
min   -8.469853e+00  5.905030e-09 -1.999987e-01  1.203604e-08  1.688394e-07   
25%    8.155429e-03  3.227379e-02  2.824387e-01  2.609341e-03  2.066730e-01   
50%    2.851613e-02  2.352318e-01  2.897158e-01  5.221295e-03  6.466099e-01   
75%    1.005583e-01  7.006623e-01  4.486980e-01  7.833949e-03  1.003266e+00   
max    5.501152e+01  1.010000e+00  3.801432e+00  3.302694e+02  1.010000e+00   
std    2.834396e-01  3.712052e-01  1.908349e-01  4.498371e-01  3.656626e-01   

               S_12           R_6          S_13          B_21          D_71  \
count  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06  3.486098e+06   
mean   2.403326e-01  5.880440e-02  2.547088e-01  5.326039e-02  7.098592e-02   
min   -4.035280e-01  4.650681e-10  3.655658e-09  4.426753e-09  3.026939e-09   
25%    1.868973e-01  2.592559e-03  4.899505e-03  2.552201e-03  8.630219e-03   
50%    1.908278e-01  5.187445e-03  9.799538e-03  5.104052e-0

In [33]:
# Pivot the data to create a 3D array
train_data_3d = train_data_filtered_oh.set_index(['customer_ID', 'end_of_month']).sort_index()

In [34]:
train_targets.head()

customer_ID end_of_month  target
0  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-03-31       0
1  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-04-30       0
2  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-05-31       0
3  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-06-30       0
4  0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2017-07-31       0

In [35]:
train_data_3d.head(13)

D_39  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.001733   
                                                   2017-04-30    0.005775   
                                                   2017-05-31    0.091505   
                                                   2017-06-30    0.002455   
                                                   2017-07-31    0.002483   
                                                   2017-08-31    0.001746   
                                                   2017-09-30    0.002183   
                                                   2017-10-31    0.003029   
                                                   2017-11-30    0.009896   
                                                   2017-12-31    0.001082   
                                                   2018-01-31    0.005715   
                                                   2018-02-28    0.002425   
                                                   2018-03-31    0.009119   

                                                                      B_1  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.008724   
                                                   2017-04-30    0.004923   
                                                   2017-05-31    0.021655   
                                                   2017-06-30    0.013683   
                                                   2017-07-31    0.015193   
                                                   2017-08-31    0.007863   
                                                   2017-09-30    0.018859   
                                                   2017-10-31    0.014324   
                                                   2017-11-30    0.016888   
                                                   2017-12-31    0.001930   
                                                   2018-01-31    0.002829   
                                                   2018-02-28    0.019837   
                                                   2018-03-31    0.009382   

                                                                      R_1  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.009228   
                                                   2017-04-30    0.006151   
                                                   2017-05-31    0.006815   
                                                   2017-06-30    0.001373   
                                                   2017-07-31    0.007605   
                                                   2017-08-31    0.004220   
                                                   2017-09-30    0.004509   
                                                   2017-10-31    0.000263   
                                                   2017-11-30    0.001789   
                                                   2017-12-31    0.001772   
                                                   2018-01-31    0.008175   
                                                   2018-02-28    0.000607   
                                                   2018-03-31    0.006104   

                                                                      B_4  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.080986   
                                                   2017-04-30    0.069419   
                                                   2017-05-31    0.068839   
                                                   2017-06-30    0.055630   
                                                   2017-07-31    0.038862   
                                                   2017-08-31 

In [36]:
# Generate a complete range of months (assuming 'end_of_month' is datetime)
all_months = pd.date_range(start=train_data_3d.index.get_level_values('end_of_month').min(),
                           end=train_data_3d.index.get_level_values('end_of_month').max(),
                           freq='M')

C:\Users\vaseekaranv\AppData\Local\Temp\ipykernel_11384\3437718540.py:2: FutureWarning: 'M' is deprecated and will be removed in a future version, please use 'ME' instead.
  all_months = pd.date_range(start=train_data_3d.index.get_level_values('end_of_month').min(),


In [37]:
all_customer_months = pd.MultiIndex.from_product(
    [train_data_3d.index.get_level_values('customer_ID').unique(), all_months],
    names=['customer_ID', 'end_of_month']
)

In [38]:
train_data_3d = train_data_3d.reindex(all_customer_months)

In [48]:
train_data_3d.head(20)

D_39  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.001733   
                                                   2017-04-30    0.005775   
                                                   2017-05-31    0.091505   
                                                   2017-06-30    0.002455   
                                                   2017-07-31    0.002483   
                                                   2017-08-31    0.001746   
                                                   2017-09-30    0.002183   
                                                   2017-10-31    0.003029   
                                                   2017-11-30    0.009896   
                                                   2017-12-31    0.001082   
                                                   2018-01-31    0.005715   
                                                   2018-02-28    0.002425   
                                                   2018-03-31    0.009119   
00001b22f846c82c51f6e3958ccd81970162bae8b007e80... 2017-03-31    0.001469   
                                                   2017-04-30    0.004229   
                                                   2017-05-31    0.003399   
                                                   2017-06-30    0.006877   
                                                   2017-07-31    0.000802   
                                                   2017-08-31    0.005366   
                                                   2017-09-30    0.005470   

                                                                      B_1  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.008724   
                                                   2017-04-30    0.004923   
                                                   2017-05-31    0.021655   
                                                   2017-06-30    0.013683   
                                                   2017-07-31    0.015193   
                                                   2017-08-31    0.007863   
                                                   2017-09-30    0.018859   
                                                   2017-10-31    0.014324   
                                                   2017-11-30    0.016888   
                                                   2017-12-31    0.001930   
                                                   2018-01-31    0.002829   
                                                   2018-02-28    0.019837   
                                                   2018-03-31    0.009382   
00001b22f846c82c51f6e3958ccd81970162bae8b007e80... 2017-03-31    0.001472   
                                                   2017-04-30    0.002125   
                                                   2017-05-31    0.003495   
                                                   2017-06-30    0.007627   
                                                   2017-07-31    0.009997   
                                                   2017-08-31    0.003352   
                                                   2017-09-30    0.006262   

                                                                      R_1  \
customer_ID                                        end_of_month             
0000099d6bd597052cdcda90ffabf56573fe9d7c79be5fb... 2017-03-31    0.009228   
                                                   2017-04-30    0.006151   
                                                   2017-05-31    0.006815   
                                                   2017-06-30    0.001373   
                                                   2017-07-31    0.007605   
                                                   2017-08-31    0.004220   
                                                   2017-09-30  

In [40]:
# Get the list of unique customer_IDs
unique_customer_ids = train_data_3d.index.get_level_values('customer_ID').unique()

# Specify the customer_ID you want to find
specific_customer_ID = 'fffb0971619564cf6a4c01cf3014e42718555728b2988ec3340c37d64db23ca1'  # Example customer_ID

# Find the position (0-based index) of the specified customer_ID
position = np.where(unique_customer_ids == specific_customer_ID)[0][0]

print(f"The position of the specified customer_ID is: {position + 1}")  # Add 1 for 1-based index

The position of the specified customer_ID is: 289097


In [41]:
# Replace 'specific_customer_ID' with the actual customer_ID you want to view
specific_customer_ID = 'fffb0971619564cf6a4c01cf3014e42718555728b2988ec3340c37d64db23ca1'  # Example customer_ID
customer_data = train_data_3d.loc[specific_customer_ID]

customer_data

D_39       B_1       R_1       B_4       B_5       R_2  \
end_of_month                                                               
2017-03-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-04-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-05-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-06-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-07-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-08-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-09-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-10-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-11-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-12-31         NaN       NaN       NaN       NaN       NaN       NaN   
2018-01-31         NaN       NaN       NaN       NaN       NaN       NaN   
2018-02-28         NaN       NaN       NaN       NaN       NaN       NaN   
2018-03-31    0.004122  0.006271  0.006557  0.956231  0.005876  0.009218   

                  D_47       B_7      D_51       B_9       R_3      B_10  \
end_of_month                                                               
2017-03-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-04-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-05-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-06-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-07-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-08-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-09-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-10-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-11-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-12-31         NaN       NaN       NaN       NaN       NaN       NaN   
2018-01-31         NaN       NaN       NaN       NaN       NaN       NaN   
2018-02-28         NaN       NaN       NaN       NaN       NaN       NaN   
2018-03-31    0.280411  0.603228  0.008617  0.008502  0.203525  0.028031   

                   S_5      B_11      S_6       R_4      B_12       S_8  \
end_of_month                                                              
2017-03-31         NaN       NaN      NaN       NaN       NaN       NaN   
2017-04-30         NaN       NaN      NaN       NaN       NaN       NaN   
2017-05-31         NaN       NaN      NaN       NaN       NaN       NaN   
2017-06-30         NaN       NaN      NaN       NaN       NaN       NaN   
2017-07-31         NaN       NaN      NaN       NaN       NaN       NaN   
2017-08-31         NaN       NaN      NaN       NaN       NaN       NaN   
2017-09-30         NaN       NaN      NaN       NaN       NaN       NaN   
2017-10-31         NaN       NaN      NaN       NaN       NaN       NaN   
2017-11-30         NaN       NaN      NaN       NaN       NaN       NaN   
2017-12-31         NaN       NaN      NaN       NaN       NaN       NaN   
2018-01-31         NaN       NaN      NaN       NaN       NaN       NaN   
2018-02-28         NaN       NaN      NaN       NaN       NaN       NaN   
2018-03-31    0.004136  0.002129  1.00937  0.003746  0.005717  0.005338   

                   R_5      D_58      B_14      D_60      S_11      D_65  \
end_of_month                                                               
2017-03-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-04-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-05-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-06-30         NaN       NaN       NaN       NaN       NaN       NaN   
2017-07-31         NaN       NaN       NaN       NaN       NaN       NaN   
2017-08-31         NaN       NaN       NaN       NaN       NaN       NaN   
20

In [42]:
# Convert to a 3D numpy array
train_data_3d_array = train_data_3d.to_numpy().reshape(
    len(train_data_3d.index.levels[0]),  # Number of unique customer_IDs
    len(train_data_3d.index.levels[1]),  # Number of unique end_of_month entries
    -1                                # Number of features
)

print(train_data_3d_array.shape)

(289115, 13, 86)


In [43]:
train_data_3d_array[289096,-1,:]

array([4.12199041e-03, 6.27115835e-03, 6.55673631e-03, 9.56230521e-01,
       5.87584544e-03, 9.21827368e-03, 2.80410945e-01, 6.03228033e-01,
       8.61729216e-03, 8.50167871e-03, 2.03525037e-01, 2.80310158e-02,
       4.13568970e-03, 2.12940644e-03, 1.00936973e+00, 3.74591514e-03,
       5.71741443e-03, 5.33762062e-03, 5.81439724e-03, 7.45878935e-01,
       9.08888318e-03, 7.13860290e-03, 2.88033098e-01, 7.38704251e-03,
       4.09799069e-01, 1.90227658e-01, 1.95411965e-04, 9.80293658e-03,
       1.26664597e-03, 8.66232440e-03, 5.05209386e-01, 6.46506071e-01,
       9.59233224e-01, 4.71785605e-01, 8.03609320e-04, 5.67617943e-04,
       1.64574618e-03, 8.65259394e-03, 7.32849631e-03, 1.23869162e-03,
       5.07654448e-04, 1.00886059e+00, 7.17743993e-01, 6.30840845e-03,
       8.21481459e-04, 6.29911153e-03, 7.46001909e-03, 8.61075055e-03,
       7.16255466e-03, 4.54526488e-03, 9.37503111e-03, 1.00000000e+00,
       5.10390336e-03, 9.71334614e-03, 5.73766883e-03, 5.01663843e-03,
      

In [44]:
val_data_3d = val_data_filtered_oh.set_index(['customer_ID', 'end_of_month']).sort_index()

all_customer_months = pd.MultiIndex.from_product(
    [val_data_3d.index.get_level_values('customer_ID').unique(), all_months],
    names=['customer_ID', 'end_of_month']
)

val_data_3d = val_data_3d.reindex(all_customer_months)

val_data_3d_array = val_data_3d.to_numpy().reshape(
    len(val_data_3d.index.levels[0]),  # Number of unique customer_IDs
    len(val_data_3d.index.levels[1]),  # Number of unique end_of_month entries
    -1                                # Number of features
)

print(val_data_3d_array.shape)

(32124, 13, 86)


In [45]:
test_data_3d = test_data_filtered_oh.set_index(['customer_ID', 'end_of_month']).sort_index()

all_customer_months = pd.MultiIndex.from_product(
    [test_data_3d.index.get_level_values('customer_ID').unique(), all_months],
    names=['customer_ID', 'end_of_month']
)

test_data_3d = test_data_3d.reindex(all_customer_months)

test_data_3d_array = test_data_3d.to_numpy().reshape(
    len(test_data_3d.index.levels[0]),  # Number of unique customer_IDs
    len(test_data_3d.index.levels[1]),  # Number of unique end_of_month entries
    -1                                # Number of features
)
print(test_data_3d_array.shape)

(137674, 13, 86)


In [46]:
train_targets[train_targets['end_of_month'] == '2018-03-31'].shape, val_targets[val_targets['end_of_month'] == '2018-03-31'].shape, test_targets[test_targets['end_of_month'] == '2018-03-31'].shape

((289115, 3), (32124, 3), (137674, 3))

In [47]:
train_targets[train_targets['end_of_month'] == '2018-03-31'].head()

customer_ID end_of_month  target
12   0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...   2018-03-31       0
38   00001b22f846c82c51f6e3958ccd81970162bae8b007e8...   2018-03-31       0
77   000084e5023181993c2e1b665ac88dbb1ce9ef621ec537...   2018-03-31       0
90   000098081fde4fd64bc4d503a5d6f86a0aedc425c96f52...   2018-03-31       0
116  0000f99513770170a1aba690daeeb8a96da4a39f11fc27...   2018-03-31       1

In [86]:
train_targets[train_targets['end_of_month'] == '2018-03-31'].to_parquet('../../data/3d_array/train_targets.parquet', index=False)
val_targets[val_targets['end_of_month'] == '2018-03-31'].to_parquet('../../data/3d_array/val_targets.parquet', index=False)
test_targets[test_targets['end_of_month'] == '2018-03-31'].to_parquet('../../data/3d_array/test_targets.parquet', index=False)

In [87]:
import h5py

with h5py.File('../../data/3d_array/mod_train_data_3d_h5.h5', 'w') as f:
    f.create_dataset('train_data_3d', data=train_data_3d_array, compression='gzip')

with h5py.File('../../data/3d_array/mod_val_data_3d_h5.h5', 'w') as f:
    f.create_dataset('val_data_3d', data=val_data_3d_array, compression='gzip')

with h5py.File('../../data/3d_array/mod_test_data_3d_h5.h5', 'w') as f:
    f.create_dataset('test_data_3d', data=test_data_3d_array, compression='gzip')